In [1]:
from matplotlib import pyplot as plt
import os
import csv
import pandas as pd
import numpy as np
from sklearn.mixture import GaussianMixture
from scipy.stats import multivariate_normal

In [2]:
file_path = 'hand_labels_hsv_train_old.csv'

df = pd.read_csv(file_path)
df['SH'] = (df['H'] + 90) % 180

X_train = df[['H', 'S', 'V']]  

In [3]:
# Initialize and fit the GaussianMixture model
n_components = 4
gmm = GaussianMixture(n_components=n_components, random_state=0)
gmm.fit(X_train)

means = gmm.means_
covariances = gmm.covariances_

def score(x_i):
    """x_i should be in shape of (n, # of features)"""
    assert np.shape(x_i)[1] == 3
    log_likelihood = gmm.score_samples(x_i)
    likelihood = np.exp(log_likelihood)
    return likelihood

## another possible but unused scoring method
def get_prob(x):
    return sum([multivariate_normal(mean=means[i], cov=covariances[i]).pdf(x) for i in range(gmm.n_components)])


In [11]:
abc = np.array([221, 65, 45]).reshape(1, -1)
print(abc)

[[221  65  45]]


In [4]:
##### Lookup table for prediction phase #####
# Convert HSV values to 5-bit equivalents
def hsv_to_5bit(h, s, v):
    h_5bit = int((h / 180.0) * 31)  # Hue range of 0-180
    s_5bit = int((s / 255.0) * 31)  # Saturation range of 0-255
    v_5bit = int((v / 255.0) * 31)  # Value range of 0-255
    return h_5bit, s_5bit, v_5bit

def five_bit_to_hsv(h_5bit, s_5bit, v_5bit):
    # Convert back from 5-bit to original HSV scale
    h = (h_5bit / 31.0) * 180  
    s = (s_5bit / 31.0) * 255 
    v = (v_5bit / 31.0) * 255
    return h, s, v

# Function to initialize the 32x32x32 lookup table
def create_lookup_table():
    lookup_table = np.zeros((32, 32, 32), dtype=np.float64)  # Using float64 to maintain small values
    for h5 in range(32):
        for s5 in range(32):
            for v5 in range(32):
                h, s, v = five_bit_to_hsv(h5, s5, v5)
                x = np.array([h, s, v], dtype=np.float64).reshape(1, -1)
                # filling in the lookup table with sum of gaussian pdf values
                lookup_table[h5, s5, v5] = score(x)[0]
    return lookup_table

# Function to query the lookup table with HSV values
def query_lookup_table(h, s, v, lookup_table):
    h_5bit, s_5bit, v_5bit = hsv_to_5bit(h, s, v)
    return lookup_table[h_5bit, s_5bit, v_5bit]

lookup_table = create_lookup_table()
print("Lookup table:", lookup_table)
print("Lookup table max:", np.max(lookup_table))


# for pdf in lookup_table.flatten():
#     if pdf > 0:
#         print("nonzero pdf: ", pdf)

/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/tho

Lookup table: [[[3.32575970e-70 1.06483641e-67 2.83291212e-65 ... 3.30279855e-30
   4.91429733e-30 6.07573687e-30]
  [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
   0.00000000e+00 0.00000000e+00]
  [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
   0.00000000e+00 0.00000000e+00]
  ...
  [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
   0.00000000e+00 0.00000000e+00]
  [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
   0.00000000e+00 0.00000000e+00]
  [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
   0.00000000e+00 0.00000000e+00]]

 [[1.14738598e-78 6.63464346e-76 3.18774682e-73 ... 3.17296597e-31
   8.52630337e-31 1.90376935e-30]
  [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
   0.00000000e+00 0.00000000e+00]
  [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e+00
   0.00000000e+00 0.00000000e+00]
  ...
  [0.00000000e+00 0.00000000e+00 0.00000000e+00 ... 0.00000000e

/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/thomaswiener/miniconda3/lib/python3.11/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but GaussianMixture was fitted with feature names
  warnings.warn(
/Users/tho

In [5]:
##### Save Lookup Table to file ####
fn = 'lookup_table_builtin'

np.save(f'{fn}.npy', lookup_table)

## saving flattened version to .txt file
lookup_table_flattened = lookup_table.flatten()
np.savetxt(f'{fn}.txt', lookup_table_flattened)